# Capstone Project - The Battle of Neighborhoods

## Choosing the Best Location for a Fast Food Restaurant in New York City

### 1- Introduction / Business Problem

The "Big Apple," the "City That Never Sleeps" New York is a city of superlatives: America's biggest; its most exciting; its business and cultural capitals; the nation's trendsetter. The city seems to pull in the best and the brightest from every corner of the country. The city's ethnic flavor has been nuanced by decades of immigrants whose first glimpse of America was the Statue of Liberty guarding New York Harbor and by large expatriate communities such as the United Nations headquartered there. For all its eight million residents, New York remains a city of neighborhoods, whether it's avant-garde Greenwich Village, bustling Harlem, the ultra-sophisticated TriBeCa, or one of the ethnic enclaves such as Little Italy or Chinatown. And a cleaner, brighter, safer New York is attracting people from around the world who are coming to enjoy the city's renaissance.

Opening a restaurant is all about location, location, location. However, not every restaurant is suitable for every location, and vice versa. It comes down to a combination of restaurant concept and ideal customer. If you can define your restaurant type and identify your target demographic and its most populated areas, you’ll be well on your way to choosing a restaurant location that sets your business up for success.

Fast food restaurant customers are 15-35 age range, spontaneous and not planned, often connected to another activity like shopping or an evening out with friends. Lower income profile, high population density and high foot traffic are all key considerations.

This project is important for businessmen and entrepreneurs who are interested in opening a fast food restaurant in NYC. In this project, we will analyze the neighborhood of NYC to choose the best location to open a fast food restaurant.

### 2- Data

New York neighborhood has a total of 5 boroughs and 306 neighborhoods. Dataset of the boroughs and neighborhoods is available on the web at https://geo.nyu.edu/catalog/nyu_2451_34572. Latitude and longitude values of NYC and its neighborhood will be gotten from *geopy* library. *Foursquare API* will be used to explore the venues in each neighborhood. Python libraries such as *Pandas*, *Numpy*, *Json*, ...etc. will be used to analyze the data and get the results.

##### Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.0.2p             |       h470a237_1         3.1 MB  conda-forge
    certifi-2018.10.15         |        py36_1000         138 KB  conda-forge
    geopy-1.17.0               |             py_0          49 KB  conda-forge
    ca-certificates-2018.10.15 |       ha4d7672_0         135 KB  conda-forge
    conda-4.5.11               |        py36_1000         651 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         4.1 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0            conda-forge
    geopy:           

### 3- Methodology

I will use the dataset of New York City boroughs and neighborhoods available on the web at https://geo.nyu.edu/catalog/nyu_2451_34572. I will get the latitude and longitude values of NYC and its neighborhood from geopy library, and use Foursquare API to explore the venues in each neighborhood and their categories.

Then, I will calculate the frequency of occurrence of each venue category and extract the 5 most common venues in each neighborhood. I will make a list of some venues that feature the neighborhood, and compare this list with each neighborhood most common venues. The neighborhoods that match one or more featured venues will be our target to open the restaurant.


#### Download and Explore Dataset

In [2]:
# Downloading data
!wget -q -O 'newyork_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print('Data downloaded!')

Data downloaded!


In [3]:
# Loading data
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
# Define a new variable that includes the data in the "Features" key
neighborhoods_data = newyork_data['features']

# Explore the first item in the list
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a *pandas* dataframe

In [5]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [6]:
# Loop through the data and fill the dataframe one row at a time
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [7]:
# Examine the resulting dataframe
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

#### Use geopy library to get the latitude and longitude values of New York City.

In [8]:
address = 'New York City, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


#### Data Preparation and Modeling

In [9]:
# The code was removed by Watson Studio for sharing.

CLIENT_ID: ID1DSZTLUTW04GUTT2CWNYWMPLSCAADHIUHX1XBK5ZRDDUKW
CLIENT_SECRET:ECCUJNFOECQBHWTMYAUPCNZUPA2DUSKXEHCT5R5DHOOIIRKB


In [10]:
# Create a function to explore the venues in New York neighborhoods

LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
                    
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [11]:
# Use the above function and create a new dataframe for New York venues

ny_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )
ny_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896521       -73.844680   
2  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
3                         Carvel Ice Cream       40.890487       -73.848568   
4                            Dunkin Donuts       40.890631       -73.849027   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2  Caribbean Restaurant  
3        Ice Cream Shop  
4            Donut Shop

In [12]:
# Check how many unique venue categories
print('There are {} uniques categories.'.format(len(ny_venues['Venue Category'].unique())))

There are 431 uniques categories.


#### Analyze Each Neighborhood

In [13]:
# one hot encoding
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = ny_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  Airport Tram  American Restaurant  \
0                   0                 0             0                    0   
1                   0                 0             0                    0   
2                   0                 0             0                    0   
3                   0                 0             0                    0   
4                   0                 0             0                    0   

   Animal Shelter  Antique Shop  Arcade  Arepa Restaurant  \
0               0             0       0                 0   
1               0             0       0                 0   
2               0             0       0                 0   
3               0             0       0                 0   
4               0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                     0                 0                   0           0   
1                     0                 0                   0           0   
2                     0                 0                   0           0   
3                     0                 0                   0           0   
4                     0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Dealership  Auto Garage  \
0                      0                    0                0            0   
1                      0                    0                0            0   
2                      0                    0                0            0   
3                      0                    0                0            0   
4                      0                    0                0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0      0          0                0         0            0           0   
1      0          0                0         0            0           0   
2      0          0                0         0            0           0   
3      0          0                0         0            0           0   
4      0

In [14]:
# Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.019608   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013514           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.076923           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.023256           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030000           0.000000   
44             Carroll Gardens     0.010000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.031915           0.000000   
59                  Co-op City     0.000000           0.07

In [15]:
# Sorting the venues in decending order and create a new dataframe for the top 5 venues of each neighborhood
num_top_venues = 5

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood            1st Most Common Venue  \
0                     Allerton                      Pizza Place   
1                     Annadale                    Deli / Bodega   
2                Arden Heights                         Pharmacy   
3                    Arlington                         Bus Stop   
4                     Arrochar                         Bus Stop   
5                      Arverne                        Surf Spot   
6                      Astoria        Middle Eastern Restaurant   
7              Astoria Heights                    Deli / Bodega   
8                   Auburndale           Furniture / Home Store   
9                   Bath Beach                         Pharmacy   
10           Battery Park City                      Coffee Shop   
11                   Bay Ridge               Italian Restaurant   
12                 Bay Terrace                   Clothing Store   
13                  Baychester                             Bank   
14                     Bayside                              Bar   
15                   Bayswater                             Park   
16                Bedford Park                      Pizza Place   
17          Bedford Stuyvesant                      Coffee Shop   
18                  Beechhurst                      Yoga Studio   
19                    Bellaire                    Deli / Bodega   
20                Belle Harbor                         Boutique   
21                   Bellerose                      Pizza Place   
22                     Belmont               Italian Restaurant   
23                 Bensonhurst                              Spa   
24                Bergen Beach                  Harbor / Marina   
25                  Blissville                    Deli / Bodega   
26                  Bloomfield                   Discount Store   
27                 Boerum Hill                      Coffee Shop   
28                Borough Park                         Pharmacy   
29                Breezy Point              Monument / Landmark   
30                   Briarwood                    Deli / Bodega   
31              Brighton Beach      Eastern European Restaurant   
32               Broad Channel                         Dive Bar   
33           Broadway Junction                            Diner   
34                   Bronxdale               Italian Restaurant   
35            Brooklyn Heights                      Yoga Studio   
36                  Brookville                           Market   
37                 Brownsville                             Park   
38                  Bulls Head                      Pizza Place   
39                    Bushwick                              Bar   
40                Butler Manor                             Pool   
41             Cambria Heights             Caribbean Restaurant   
42                    Canarsie             Caribbean Restaurant   
43               Carnegie Hill                      Pizza Place   
44             Carroll Gardens               Italian Restaurant   
45                 Castle Hill                      Pizza Place   
46           Castleton Corners                      Pizza Place   
47              Central Harlem               African Restaurant   
48                  Charleston                       Shoe Store   
49                     Chelsea               Italian Restaurant   
50                   Chinatown               Chinese Restaurant   
51                 City Island                  Harbor / Marina   
52                   City Line                       Donut Shop   
53                Civic Center             Gym / Fitness Center   
54           Claremont Village                      Bus Station   
55                Clason Point                             Park   
56                     Clifton                    Grocery Store   
57                     Clinton                          Theater   
58                Clinton Hill                      Pizza Place  

In [16]:
# Group the most common venues in one column
source_col_loc = neighborhoods_venues_sorted.columns.get_loc('Neighborhood')
neighborhoods_venues_sorted['Most Common Venues'] =\
neighborhoods_venues_sorted.iloc[:,source_col_loc+1:source_col_loc+6].apply(lambda x: ", ".join(x.astype(str)), axis=1)

# Drop the splitted most common venues columns
venues_grouped = neighborhoods_venues_sorted
col = ['1st Most Common Venue', '2nd Most Common Venue', '3rd Most Common Venue', '4th Most Common Venue', '5th Most Common Venue']
venues_grouped = venues_grouped.drop(col, axis=1)
venues_grouped.head()

Neighborhood                                 Most Common Venues
0       Allerton  Pizza Place, Deli / Bodega, Chinese Restaurant...
1       Annadale  Deli / Bodega, Cosmetics Shop, Train Station, ...
2  Arden Heights  Pharmacy, Deli / Bodega, Pizza Place, Coffee S...
3      Arlington  Bus Stop, Intersection, Boat or Ferry, Playgro...
4       Arrochar  Bus Stop, Italian Restaurant, Pizza Place, Del...

In [17]:
# Convert the most common venues to lists
for i in range(venues_grouped['Most Common Venues'].count()):
    venues_grouped['Most Common Venues'][i] = list(venues_grouped['Most Common Venues'][i].split(", "))
venues_grouped.head()

Neighborhood                                 Most Common Venues
0       Allerton  [Pizza Place, Deli / Bodega, Chinese Restauran...
1       Annadale  [Deli / Bodega, Cosmetics Shop, Train Station,...
2  Arden Heights  [Pharmacy, Deli / Bodega, Pizza Place, Coffee ...
3      Arlington  [Bus Stop, Intersection, Boat or Ferry, Playgr...
4       Arrochar  [Bus Stop, Italian Restaurant, Pizza Place, De...

### 4- Results

After the above analysis, we made a dataframe contains the neighborhoods and their most common venues. Now, I will compare the most common venues with the featured venues lest, and drop the rows that don’t match the list. The result will be a dataframe contains only the neighborhoods that include featured venues, which is our target.

In [18]:
# Compare the most common venues with the selected venues fit with our criteria
featured_venues = ['Coffee Shop', 'Café', 'Park', 'Hotel', 'Sandwich Place', 'Pizza Place', 'Gym / Fitness Center', 'Exhibit',\
              'Gym', 'Supermarket', 'Nightclub', 'Concert Hall', 'Jazz Club', 'Train Station', 'Metro Station', 'Theater', ]
venues_grouped["Neighborhood Fit"] = ""
for i in range(0, venues_grouped['Most Common Venues'].count()):
    for item in venues_grouped['Most Common Venues'][i]:
        if item in featured_venues:
            venues_grouped["Neighborhood Fit"][i] = 'True'
            
venues_grouped      

Neighborhood  \
0                     Allerton   
1                     Annadale   
2                Arden Heights   
3                    Arlington   
4                     Arrochar   
5                      Arverne   
6                      Astoria   
7              Astoria Heights   
8                   Auburndale   
9                   Bath Beach   
10           Battery Park City   
11                   Bay Ridge   
12                 Bay Terrace   
13                  Baychester   
14                     Bayside   
15                   Bayswater   
16                Bedford Park   
17          Bedford Stuyvesant   
18                  Beechhurst   
19                    Bellaire   
20                Belle Harbor   
21                   Bellerose   
22                     Belmont   
23                 Bensonhurst   
24                Bergen Beach   
25                  Blissville   
26                  Bloomfield   
27                 Boerum Hill   
28                Borough Park   
29                Breezy Point   
30                   Briarwood   
31              Brighton Beach   
32               Broad Channel   
33           Broadway Junction   
34                   Bronxdale   
35            Brooklyn Heights   
36                  Brookville   
37                 Brownsville   
38                  Bulls Head   
39                    Bushwick   
40                Butler Manor   
41             Cambria Heights   
42                    Canarsie   
43               Carnegie Hill   
44             Carroll Gardens   
45                 Castle Hill   
46           Castleton Corners   
47              Central Harlem   
48                  Charleston   
49                     Chelsea   
50                   Chinatown   
51                 City Island   
52                   City Line   
53                Civic Center   
54           Claremont Village   
55                Clason Point   
56                     Clifton   
57                     Clinton   
58                Clinton Hill   
59                  Co-op City   
60                 Cobble Hill   
61               College Point   
62                     Concord   
63                   Concourse   
64           Concourse Village   
65                Coney Island   
66                      Corona   
67                Country Club   
68               Crown Heights   
69               Cypress Hills   
70                 Ditmas Park   
71                Dongan Hills   
72                  Douglaston   
73                    Downtown   
74                       Dumbo   
75               Dyker Heights   
76               East Elmhurst   
77               East Flatbush   
78                 East Harlem   
79               East New York   
80                East Tremont   
81                East Village   
82           East Williamsburg   
83                 Eastchester   
84                    Edenwald   
85                    Edgemere   
86              Edgewater Park   
87                 Egbertville   
88                    Elm Park   
89                    Elmhurst   
90                 Eltingville   
91                Emerson Hill   
92                     Erasmus   
93                Far Rockaway   
94                   Fieldston   
95          Financial District   
96                    Flatbush   
97                    Flatiron   
98                   Flatlands   
99                 Floral Park   
100                   Flushing   
101                    Fordham   
102               Forest Hills   
103       Forest Hills Gardens   
104                Fort Greene   
105              Fort Hamilton   
106                  Fox Hills   
107              Fresh Meadows   
108               Fulton Ferry   
109                 Georgetown   
110            Gerritsen Beach   
111                  Glen Oaks   
112                   Glendale   
113                    Gowanus   
114                   Gramercy   
115               Graniteville   
116                 Grant City   
117   

In [19]:
filter = venues_grouped["Neighborhood Fit"] != ""
target_neighborhood = venues_grouped[filter]
target_neighborhood.head()

Neighborhood                                 Most Common Venues  \
0       Allerton  [Pizza Place, Deli / Bodega, Chinese Restauran...   
1       Annadale  [Deli / Bodega, Cosmetics Shop, Train Station,...   
2  Arden Heights  [Pharmacy, Deli / Bodega, Pizza Place, Coffee ...   
4       Arrochar  [Bus Stop, Italian Restaurant, Pizza Place, De...   
5        Arverne  [Surf Spot, Metro Station, Board Shop, Pizza P...   

  Neighborhood Fit  
0             True  
1             True  
2             True  
4             True  
5             True

In [20]:
print('There number of neighborhoods fit in our selection criteria is {} neighborhoods.'.format(target_neighborhood['Neighborhood'].count()))

There number of neighborhoods fit in our selection criteria is 214 neighborhoods.


In [21]:
target_neighborhood.reset_index(drop=True, inplace=True)
print('The best neighborhoods to open a fastfood restaurant in New York are:\n{}'.format(target_neighborhood['Neighborhood']))

The best neighborhoods to open a fastfood restaurant in New York are:
0                       Allerton
1                       Annadale
2                  Arden Heights
3                       Arrochar
4                        Arverne
5                     Auburndale
6              Battery Park City
7                      Bay Ridge
8                    Bay Terrace
9                     Baychester
10                     Bayswater
11                  Bedford Park
12            Bedford Stuyvesant
13                    Beechhurst
14                     Bellerose
15                       Belmont
16                   Bensonhurst
17                  Bergen Beach
18                    Blissville
19                   Boerum Hill
20                  Borough Park
21                 Broad Channel
22             Broadway Junction
23              Brooklyn Heights
24                   Brownsville
25                    Bulls Head
26                      Bushwick
27               Cambria Heights
28    

### 5- Discussion

In this project, I analyzed the neighborhoods of NYC using a prepared dataset, and analyzed the venues using geopy and Foursquare API, extracted the most common venues and chose the neighborhoods that contains featured venues using Pandas and Numpy. I concluded a list of 214 neighborhoods in NYC where it is suitable to open a fast food restaurant.

### 6- Conclusion

After the analysis done in Methodology section and the last list in Results section, i concluded to 214 neighborhoods in NYC that have featured venues. The result list is the suitable neighborhoods to open a fast food restaurant.